## Imports

In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
import gc
import hashlib
import json
import os
import random
from contextlib import nullcontext
from typing import Literal, Optional

import numpy as np
import torch
import torch.distributed as dist
import torch.nn.functional as F
from datasets import Dataset
from jaxtyping import Float
from safetensors import safe_open
from safetensors.torch import load_file, save_file
from torch import Tensor

from tqdm.auto import tqdm
from transformers import PreTrainedModel

from bergson.collection import collect_gradients
from bergson.data import DataConfig, IndexConfig, create_index, load_gradients, pad_and_tensor
from bergson.distributed import distributed_computing, setup_data_pipeline
from bergson.gradients import (
    GradientProcessor,
)
from bergson.hessians.collector import EkfacCollector
from bergson.hessians.logger import get_logger

In [4]:
def _projection(
    name: str,
    m: int,
    n: int,
    device: str,
    side: Literal["left", "right"],
    dtype: torch.dtype,
) -> Tensor:
    """Return the `side` projection matrix for parameter `name` of shape [m, n]."""
    # Seed the PRNG with the name of the layer and what "side" we are projecting
    message = bytes(f"{name}/{side}", "utf-8")
    digest = hashlib.md5(message).digest()
    seed = int.from_bytes(digest, byteorder="big") % (2**63 - 1)
    prng = torch.Generator(device).manual_seed(seed)

    A = torch.randn(m, n, device=device, dtype=dtype, generator=prng)
    A /= A.norm(dim=1, keepdim=True)
    return A

## -1. Compute gradients

In [4]:
test_path = "/root/bergson/tests/ekfac_tests/test_files/pile_10k_examples"
test_gradients_path = test_path + "/test_gradients"

In [5]:
cfg_json = json.load(open(os.path.join(test_path, "ground_truth", "index_config.json"), "r"))
cfg = IndexConfig(**cfg_json)
cfg.data = DataConfig(**(cfg_json["data"]))
original_proj_dim = cfg.projection_dim

In [6]:
data = setup_data_pipeline(cfg)
assert isinstance(data, Dataset)
data = data.select(range(10))  # only a small number of examples since we also want to store uncompressed gradients
# save data to test_gradients_path
test_gradients_path_data = os.path.join(test_gradients_path, "gradient_data")
data.save_to_disk(test_gradients_path_data)

Saving the dataset (0/1 shards):   0%|          | 0/10 [00:00<?, ? examples/s]

In [7]:
cfg.ekfac = True
cfg.skip_preconditioners = True
cfg.world_size = 1
cfg.data.dataset = test_gradients_path_data
cfg.data.completion_column = ""
cfg.data.conversation_column = ""


In [8]:
# Run compressed version
cfg.run_path = test_gradients_path + "/proj_dim_16"
cfg.projection_dim = 16

distributed_computing(
    cfg=cfg,
    worker_fn=collect_gradients,
)

Building index:   0%|          | 0/2 [00:00<?, ?it/s]

Saving the dataset (0/1 shards):   0%|          | 0/10 [00:00<?, ? examples/s]

In [9]:
# Run uncompression version
cfg.run_path = test_gradients_path + "/proj_dim_0"
cfg.projection_dim = 0
distributed_computing(
    cfg=cfg,
    worker_fn=collect_gradients,
)

Building index:   0%|          | 0/2 [00:00<?, ?it/s]

Saving the dataset (0/1 shards):   0%|          | 0/10 [00:00<?, ? examples/s]

## 0. Load EKFAC

In [10]:
influence_path = test_path + "/run/influence_results"

# all paths inside ekfac_path
world_size = len(os.listdir(influence_path + "/activation_covariance_sharded"))


In [11]:
def merge_shards(path: str):
    shard_paths = [path + f"/shard_{rank}.safetensors" for rank in range(world_size)]
    shard_factor = [load_file(path, device="cuda") for path in shard_paths]
    tensor_dict = {}
    for k, v in shard_factor[0].items():
        tensor_dict[k] = torch.cat([shard_factor[rank][k] for rank in range(world_size)], dim=0)
    return tensor_dict

In [12]:
eigen_a_full = merge_shards(influence_path + "/activation_eigen_sharded")
eigen_g_full = merge_shards(influence_path + "/gradient_eigen_sharded")
lambda_factor_full = merge_shards(influence_path + "/eigenvalue_correction_sharded")

## 1. Load the gradient


In [13]:
gradient_path_16 = test_gradients_path + "/proj_dim_16"

mmap_16 = load_gradients(gradient_path_16)
with open(os.path.join(gradient_path_16, "info.json")) as f:
    info = json.load(f)


In [14]:
gradient_path_0 = test_gradients_path + "/proj_dim_0"
mmap_0 = load_gradients(gradient_path_0)
with open(os.path.join(gradient_path_0, "info.json")) as f:
    info_0 = json.load(f)

## 2. Apply EKFAC

In [15]:
names = eigen_a_full.keys()

In [16]:
def apply_ekfac_module(gradient, eigen_a, eigen_g, lambda_matrix, proj_right, proj_left):
    """Apply EKFAC preconditioning to a gradient.

    Args:
        gradient: A tensor of shape [out_features, in_features].
        eigen_a: Eigenvectors of the activation covariance, shape [in_features, r].
        eigen_g: Eigenvectors of the gradient covariance, shape [out_features, r].
        lambda_matrix: Eigenvalue correction matrix, shape [r, r].

    Returns:
        The preconditioned gradient of shape [out_features, in_features].
    """
    # Project the gradient into the subspace defined by eigen_a and eigen_g
    projected = eigen_g.T @ gradient @ eigen_a  # Shape: [r, r]
    corrected = projected
    # Apply the eigenvalue correction
    inverse_lambda = (lambda_matrix + cfg.lambda_damp_factor * lambda_matrix.mean()).reciprocal()

    # print(f"{lambda_matrix.mean().item()}")
    # for i in range(8):
    #     shard_size = lambda_matrix.shape[0] // 8
    #     start = i * shard_size
    #     end = start + shard_size
    #     shard = lambda_matrix[start:end]
    #     shard_mean = shard.mean()
    #     print(f"y_{i}= {shard_mean.item()}")

    corrected = projected * inverse_lambda  # Element-wise multiplication

    # Reconstruct the preconditioned gradient
    preconditioned = eigen_g @ corrected @ eigen_a.T  # Shape: [o, i]

    projected = proj_left @ preconditioned @ proj_right.T

    return projected

In [17]:
preconditioned_grad_dict = {}
for name in names:
    eigen_a_tensor = eigen_a_full[name]
    eigen_g_tensor = eigen_g_full[name]
    lambda_tensor = lambda_factor_full[name]

    i, o = eigen_a_tensor.shape[0], eigen_g_tensor.shape[0]
    gradient_tensor = torch.from_numpy(mmap_0[name].copy()).to("cuda", dtype=eigen_a_full[name].dtype).view(-1, o, i)

    proj_pi = _projection(
        name,
        original_proj_dim,  # type: ignore
        i,
        device="cuda",
        side="right",
        dtype=eigen_a_full[name].dtype,
    )

    proj_qo = _projection(
        name,
        original_proj_dim,  # type: ignore
        o,
        device="cuda",
        side="left",
        dtype=eigen_g_full[name].dtype,
    )
    preconditioned_gradient = apply_ekfac_module(
        gradient_tensor,
        eigen_a_tensor,
        eigen_g_tensor,
        lambda_tensor,
        proj_pi,
        proj_qo,
    )
    preconditioned_grad_dict[name] = preconditioned_gradient


In [18]:
preconditioned_grad_dict

{'layers.0.mlp.dense_4h_to_h': tensor([[[-1.2779e+04, -2.7577e+04,  1.8280e+04,  ..., -4.9049e+04,
            5.4152e+04,  1.8486e+04],
          [-8.0817e+04,  1.2589e+03, -6.4973e+03,  ...,  2.0937e+04,
            2.0420e+03,  4.1905e+04],
          [ 9.6400e+04,  4.5624e+04,  2.7050e+04,  ..., -2.3069e+04,
           -4.0305e+03,  6.6471e+02],
          ...,
          [ 5.3798e+04, -6.0532e+03, -2.7280e+04,  ..., -3.6049e+03,
           -8.7175e+03, -8.6240e+04],
          [ 7.9193e+03, -4.6743e+03,  3.4813e+04,  ...,  1.4748e+04,
           -1.0972e+04, -8.3218e+03],
          [ 6.2506e+04,  8.2155e+03, -3.6835e+04,  ..., -2.5743e+04,
           -3.6405e+03,  2.7258e+04]],
 
         [[ 2.4812e+04,  1.0809e+05,  3.3299e+04,  ..., -4.5757e+04,
            5.8006e+04, -2.7411e+04],
          [ 9.9236e+03, -3.6270e+03, -1.2364e+05,  ...,  6.9473e+04,
            2.5321e+03, -3.0188e+03],
          [ 3.8811e+04, -5.5721e+04,  2.1230e+04,  ..., -1.6455e+04,
           -2.0905e+04, -3.

In [19]:
os.makedirs(test_gradients_path + "/gradients_after_ekfac", exist_ok=True)
save_file(preconditioned_grad_dict, test_gradients_path + "/gradients_after_ekfac" + "/gradients.safetensors")

In [20]:
dataset_path = "/mnt/ssd-1/gpaulo/emergent-misalignment/emergent-misalignment-eleuther/open_models/merged_medical_completions_llama.jsonl"
dataset = Dataset.from_json(dataset_path)
# save first 10 entries
dataset = dataset.select(range(4800))
dataset.save_to_disk(test_gradients_path + "/dataset")

Saving the dataset (0/1 shards):   0%|          | 0/4800 [00:00<?, ? examples/s]

In [21]:
g_path = "/root/bergson/tests/ekfac_tests/test_files/pile_10k_examples/test_gradients/proj_dim_0_ekfac"

mmap = load_gradients(g_path)

In [26]:
n, o, i = 10, 1000, 5000
matrix_noi = torch.rand(n, o, i).to("cuda")

In [27]:
start_row = 0
end_row = o // 8

inverse_lambda = torch.rand(o // 8, i).to("cuda")

In [28]:
r_1 = matrix_noi[:, start_row:end_row, :].mul(inverse_lambda)

In [29]:
r_2 = matrix_noi[0, start_row:end_row, :].mul(inverse_lambda)

In [44]:
ground_truth_path = "/root/bergson/tests/ekfac_tests/test_files/pile_10k_examples/test_gradients/gradients_after_ekfac"
run_path = "/root/bergson/tests/ekfac_tests/test_files/pile_10k_examples/test_gradients/proj_dim_0_ekfac"


ground_truth = load_file(os.path.join(ground_truth_path, "gradients.safetensors"), device="cuda")
computed_mmap = load_gradients(run_path)


In [6]:
path = "/mnt/ssd-1/louis/emergent_misalignment/test_query_ekfac"

computed_mmap = load_gradients(path)

In [9]:
names = computed_mmap.dtype.names

In [ ]:
computed_mmap

memmap([([-8.80636700e+06, -7.71734720e+07,  7.99246000e+07, -7.39820720e+07,  8.16977600e+07,  6.11757520e+07,  5.85060800e+06, -6.64050000e+07, -2.37108720e+07,  4.66395200e+07,  1.66313480e+07,  3.58145480e+07, -2.27432460e+07, -3.79388960e+07, -4.22802400e+07, -1.12688872e+08,  1.09216368e+08, -6.30218000e+05, -2.95671180e+07, -1.66740080e+07,  3.83776240e+07, -5.96850720e+07,  4.78044440e+07,  4.10923680e+07,  9.90182720e+07, -6.34359880e+07,  1.97887680e+07, -1.91186200e+06,  9.62280480e+07,  8.20882600e+06, -3.35595680e+07,  2.31384220e+07, -2.38399940e+07, -5.93423280e+07,  1.17779600e+06, -7.82044960e+07,  5.63062240e+07,  2.62221580e+07,  1.53627400e+07, -3.95639440e+07, -6.22485600e+07,  7.63058560e+07, -2.94236480e+07,  3.75896120e+07, -4.17432600e+07, -3.72924880e+07, -3.98237200e+07, -3.55634160e+07,  1.02588640e+08, -2.58975860e+07,  6.49603520e+07, -7.02707600e+07,  8.90197520e+07,  3.54732040e+07,  4.55281400e+07, -1.05685152e+08,  8.27209520e+07,  8.76295680e+07,  9.6

## Debugging minor diffs

In [45]:
k = "layers.1.mlp.dense_h_to_4h"
a, b, c = 2, 12, 15

In [46]:
ground_truth_tensor = ground_truth[k].to(dtype=torch.float32)

computed_tensor = (
    torch.from_numpy(computed_mmap[k].copy()).to(device="cuda").view(-1, *ground_truth_tensor.shape[1:])
).to(dtype=torch.float32)

In [47]:
ground_truth_tensor[a, b, c]

tensor(-16.6719, device='cuda:0')

In [48]:
computed_tensor[a, b, c]

tensor(-16.5032, device='cuda:0')

In [49]:
0.0020384215749800205 * 31493650.0

64197.33563486952

In [50]:
64197.3359375

64197.3359375

In [61]:
0.0006574208382517099 * 31493650.0

20704.581782605965

In [55]:
a = 0.0006574208382517099
b = 31493650.0

a_tensor, b_tensor = torch.tensor(a), torch.tensor(b)

In [67]:
x = a_tensor.to(torch.float64) * b_tensor.to(torch.float64)

In [72]:
-0.00041100458474829793 + 0.001573218498378992

0.0011622139136306942

: 

In [70]:
x.to(torch.float32).item()

20704.58203125